In [2]:
from sklearn.model_selection import train_test_split
import tensorflow as tf
import numpy as np
import pandas as pd
import seaborn as sns
from dys_functions import *

sns.set()

2023-08-31 09:07:40.660856: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-08-31 09:07:41.253138: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [3]:
metadata_path = './data/metadata.xlsx'
svc_path = './data/svcs/'
metadata_path_extra = './Dysgraphia-detection-through-machine-learning-main/data2_SciRep_pub.xlsx'
svc_path_extra = './Dysgraphia-detection-through-machine-learning-main/dataSciRep_public/'

data = load_data(metadata_path, metadata_path_extra, svc_path, svc_path_extra)
metadata_new, metadata_extra, svc_data, svc_indexes = data

metadata_train = pd.read_csv('train.csv').drop(columns='Unnamed: 0')
metadata_train_extra = pd.read_csv('train_extra.csv').drop(columns='Unnamed: 0')

In [4]:
metadata_train.head(5)

filename  new_class   age  sex  DYS
0   BR4428          4  10.0  1.0  0.0
1   HK1407          4  10.0  1.0  0.0
2   BR4211          2   8.0  2.0  0.0
3   BR4445          4  10.0  2.0  0.0
4   BR3301          3   9.0  1.0  0.0

Spliting the original dataset

In [5]:
X_train_orig, X_val_orig, y_train_orig, y_val_orig = train_test_split(metadata_train,
                                                                      metadata_train.DYS,
                                                                      test_size=0.1, 
                                                                      stratify=metadata_train.DYS)
X_train_orig = X_train_orig.merge(svc_indexes, how='inner', on='filename')
X_val_orig = X_val_orig.merge(svc_indexes, how='inner', on='filename')

In [18]:
X_train_orig.to_csv('train_orig.csv')
X_val_orig.to_csv('val_orig.csv')

Spliting the extra dataset

In [6]:
X_train_extra, X_val_extra, y_train_extra, y_val_extra = train_test_split(metadata_train_extra,
                                                                      metadata_train_extra.DYS,
                                                                      test_size=0.1, 
                                                                      stratify=metadata_train_extra.DYS)

In [19]:
X_train_extra.to_csv('train_extra.csv')
X_val_extra.to_csv('val_extra.csv')

#### Evaluation metrics

In [7]:
from sklearn.metrics import precision_recall_fscore_support, confusion_matrix, accuracy_score

def print_results(y_true, y_pred):
    y_pred = np.rint(y_pred)
    print(precision_recall_fscore_support(y_true, y_pred))
    return confusion_matrix(y_true, y_pred)

In [8]:
# carthesian product of (description x tablet inputs x on/off paper) + additional parameters
col_names = column_names()

split_data = [split_on_gaps(series) for series in svc_data]

# prepare the Butterworth filtered dataset
butter_data = [[filter_data(subseries) 
                for subseries in series]
               for series in split_data]

In [9]:
def train_model(train_test_splits, data, model, fit_params):
    X_train_split, X_test_split, y_train, y_test = train_test_splits
    X_train = np.take(data, X_train_split.index, axis=0).astype(float)
    X_test  = np.take(data, X_test_split.index, axis=0).astype(float)
    
    dys_weight = len(y_train)/sum(y_train)
    class_weight = {0: 1, 1: dys_weight}

    epochs, batchsize, initial_epoch, class_weight = fit_params
    
    history = model.fit(X_train,y_train, epochs=epochs,
                        batch_size=batchsize,
                        validation_data=(X_test, y_test),    
                        verbose=True,
                        initial_epoch=initial_epoch,
                        class_weight=class_weight)
    
    y_pred = model.predict(X_test)
    print_results(y_test, y_pred)
    return model, history

#### Using a simple classfier with LSTM blocks

In [49]:
def create_simple_lstm(input_shape):
    optimizer = tf.keras.optimizers.Adamax(learning_rate=0.002)
    metrics = [tf.keras.metrics.Precision(),
               tf.keras.metrics.Recall(), 
               tf.keras.metrics.AUC()]
    
    lstm = tf.keras.Sequential([
            tf.keras.layers.LSTM(80, input_shape=input_shape,
                                 return_sequences=True, dropout=0.2),
            tf.keras.layers.LSTM(50, dropout=0.2),
            tf.keras.layers.Dense(1, activation='sigmoid')])

    lstm.compile(optimizer=optimizer,
              loss=tf.losses.BinaryCrossentropy(),
              metrics=metrics)
    return lstm

In [50]:
def create_lstm(input_shape):
    optimizer = tf.keras.optimizers.Adam(learning_rate=0.002)
    metrics = [tf.keras.metrics.Precision(),
               tf.keras.metrics.Recall(), 
               tf.keras.metrics.AUC()]
    
    lstm = tf.keras.Sequential([
            tf.keras.layers.LSTM(128, input_shape=input_shape,
                                 return_sequences=True, dropout=0.2),
            tf.keras.layers.LSTM(64, dropout=0.2),
            tf.keras.layers.Dense(16),
            tf.keras.layers.Dense(1, activation='sigmoid')])

    lstm.compile(optimizer=optimizer,
              loss=tf.losses.BinaryCrossentropy(),
              metrics=metrics)
    return lstm

### Classification with sequences of length 120

Firstly trying to reproduce the previous results (#TODO cite). And a comparison of using raw data to data preprocessed with the butterworth filter.

In [11]:
raw_train120, data_index120 = prepare_dynamic_dataset(split_data, 120)

butter_train120, _ = prepare_dynamic_dataset(butter_data, 120)

X_index120 = pd.DataFrame(data_index120, columns=['fileindex']
                                   ).reset_index()

X_train120 = X_train_orig.merge(X_index120, how='inner', on='fileindex')
y_train120 = X_train120.DYS.astype(int)

X_val120 = X_val_orig.merge(X_index120, how='inner', on='fileindex')
y_val120 = X_val120.DYS.astype(int)

X_train120_extra = X_train_extra.merge(X_index120, how='inner', on='fileindex')
y_train120_extra = X_train120_extra.DYS.astype(int)

X_val120_extra = X_val_extra.merge(X_index120, how='inner', on='fileindex')
y_val120_extra = X_val120_extra.DYS.astype(int)

In [46]:
from sklearn.dummy import DummyClassifier

dummy = DummyClassifier(strategy='stratified')
dummy.fit(X_train120_extra, y_train120_extra)
y_dummy120_extra = dummy.predict(X_val120_extra)
print_results(y_val120_extra, y_dummy120_extra)
confusion_matrix(y_val120_extra, y_dummy120_extra)

(array([0.54944098, 0.45358286]), array([0.46022865, 0.54280242]), array([0.50089351, 0.49419814]), array([8222, 6787]))


array([[3784, 4438],
       [3103, 3684]])

In [12]:
lstm_raw120 = create_simple_lstm((120, 7))
class_weight = {0: 1, 1: len(y_train_orig)/sum(y_train_orig)}
fit_raw120_params = (100, 256, 0, class_weight)

metadata120_orig = (X_train120, X_val120, y_train120, y_val120)

lstm_raw120, _ = train_model(metadata120_orig, raw_train120, 
                                lstm_raw120, fit_raw120_params)

2023-08-31 09:08:47.489858: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1639] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 18337 MB memory:  -> device: 0, name: NVIDIA A100 80GB PCIe MIG 1g.20gb, pci bus id: 0000:21:00.0, compute capability: 8.0


Epoch 1/100


2023-08-31 09:08:55.399315: I tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:432] Loaded cuDNN version 8600
2023-08-31 09:08:55.489739: I tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:606] TensorFloat-32 will be used for the matrix multiplication. This will only be logged once.
2023-08-31 09:08:55.521333: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x7fe05c6eedc0 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
2023-08-31 09:08:55.521415: I tensorflow/compiler/xla/service/service.cc:176]   StreamExecutor device (0): NVIDIA A100 80GB PCIe MIG 1g.20gb, Compute Capability 8.0
2023-08-31 09:08:55.526560: I tensorflow/compiler/mlir/tensorflow/utils/dump_mlir_util.cc:255] disabling MLIR crash reproducer, set env var `MLIR_CRASH_REPRODUCER_DIRECTORY` to enable.
2023-08-31 09:08:55.590987: I tensorflow/tsl/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory


  9/785 [..............................] - ETA: 10s - loss: 1.2817 - precision: 0.1583 - recall: 0.7052 

2023-08-31 09:08:55.642353: I ./tensorflow/compiler/jit/device_compiler.h:186] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


785/785 [==============================] - 13s 14ms/step - loss: 1.2534 - precision: 0.1678 - recall: 0.8143 - val_loss: 0.7386 - val_precision: 0.2394 - val_recall: 0.5642
Epoch 2/100
785/785 [==============================] - 11s 14ms/step - loss: 1.2412 - precision: 0.1708 - recall: 0.8478 - val_loss: 0.7632 - val_precision: 0.2412 - val_recall: 0.4452
Epoch 3/100
785/785 [==============================] - 11s 14ms/step - loss: 1.2345 - precision: 0.1731 - recall: 0.8419 - val_loss: 0.7469 - val_precision: 0.2064 - val_recall: 0.4764
Epoch 4/100
785/785 [==============================] - 11s 14ms/step - loss: 1.2289 - precision: 0.1735 - recall: 0.8585 - val_loss: 0.7941 - val_precision: 0.2304 - val_recall: 0.6574
Epoch 5/100
785/785 [==============================] - 11s 14ms/step - loss: 1.2268 - precision: 0.1725 - recall: 0.8706 - val_loss: 0.7622 - val_precision: 0.2296 - val_recall: 0.4562
Epoch 6/100
785/785 [==============================] - 11s 14ms/step - loss: 1.2213 - p

In [13]:
lstm_butter120 = create_simple_lstm((120, 7))
class_weight = {0: 1, 1: len(y_train120)/sum(y_train120)}
fit_butter120_params = (100, 256, 0, class_weight)

metadata120_orig = (X_train120, X_val120, y_train120, y_val120)

lstm_butter120, _ = train_model(metadata120_orig, butter_train120, 
                                lstm_butter120, fit_butter120_params)

Epoch 1/100
785/785 [==============================] - 13s 14ms/step - loss: 1.2535 - precision_1: 0.1687 - recall_1: 0.8165 - val_loss: 0.7303 - val_precision_1: 0.2982 - val_recall_1: 0.9461
Epoch 2/100
785/785 [==============================] - 11s 14ms/step - loss: 1.2401 - precision_1: 0.1710 - recall_1: 0.8449 - val_loss: 0.7206 - val_precision_1: 0.2579 - val_recall_1: 0.7115
Epoch 3/100
785/785 [==============================] - 11s 14ms/step - loss: 1.2324 - precision_1: 0.1732 - recall_1: 0.8482 - val_loss: 0.7362 - val_precision_1: 0.2348 - val_recall_1: 0.6708
Epoch 4/100
785/785 [==============================] - 11s 14ms/step - loss: 1.2276 - precision_1: 0.1728 - recall_1: 0.8575 - val_loss: 0.7146 - val_precision_1: 0.2183 - val_recall_1: 0.4382
Epoch 5/100
785/785 [==============================] - 11s 14ms/step - loss: 1.2226 - precision_1: 0.1740 - recall_1: 0.8535 - val_loss: 0.6852 - val_precision_1: 0.2303 - val_recall_1: 0.5384
Epoch 6/100
785/785 [==============

With this dataset we were not able to reproduce the results. The model barely learns, although we can see the loss decreasing. It outperforms classifiers on extracted data, but this might simply be a consequence of the increased complexity. Also there is little difference between the results of the two preprocessing aproaches. This mirrors previous results, thus moving forward only the latter is presented.

In [26]:
lstm_butter120_extra = create_simple_lstm((120, 7))
class_weight = {0: 1, 1: len(y_train_extra)/sum(y_train_extra)}
fit_butter120_params = (100, 128, 0, class_weight)

metadata120_orig = (X_train120_extra, X_val120_extra, y_train120_extra, y_val120_extra)

lstm_butter120_extra, _ = train_model(metadata120_orig, butter_train120, 
                                lstm_butter120_extra, fit_butter120_params)

Epoch 1/100
1211/1211 [==============================] - 16s 11ms/step - loss: 0.9482 - precision_8: 0.5438 - recall_8: 0.9971 - val_loss: 0.7764 - val_precision_8: 0.4348 - val_recall_8: 0.8994
Epoch 2/100
1211/1211 [==============================] - 13s 11ms/step - loss: 0.9426 - precision_8: 0.5449 - recall_8: 0.9954 - val_loss: 0.8048 - val_precision_8: 0.4524 - val_recall_8: 0.9988
Epoch 3/100
1211/1211 [==============================] - 13s 11ms/step - loss: 0.9369 - precision_8: 0.5484 - recall_8: 0.9898 - val_loss: 0.7858 - val_precision_8: 0.4329 - val_recall_8: 0.8787
Epoch 4/100
1211/1211 [==============================] - 13s 11ms/step - loss: 0.9333 - precision_8: 0.5522 - recall_8: 0.9844 - val_loss: 0.7990 - val_precision_8: 0.4351 - val_recall_8: 0.9147
Epoch 5/100
1211/1211 [==============================] - 13s 11ms/step - loss: 0.9293 - precision_8: 0.5544 - recall_8: 0.9833 - val_loss: 0.7987 - val_precision_8: 0.4307 - val_recall_8: 0.8852
Epoch 6/100
1211/1211 [==

In [15]:
lstm_raw120.save('model_saves/lstm_rawr120.keras')
lstm_butter120.save('model_saves/lstm_butter120.keras')
lstm_butter120_extra.save('model_saves/lstm_butter120_extra.keras')

### Combined datasets

In [30]:
X_train120_combined = pd.concat([X_train120_extra, X_train120], axis=0)
X_val120_combined = pd.concat([X_val120_extra, X_val120], axis=0)
#y_train120_combined = pd.concat([y_train120_extra, y_train120], axis=0)
#y_val120_combined = pd.concat([X_val120_extra, X_val120], axis=0)

lstm_butter120_combined = create_simple_lstm((120, 7))
class_weight = {0: 1, 1: len(y_train_extra)/sum(y_train_extra)}
fit_butter120_params = (100, 128, 0, class_weight)

metadata120_combined = (X_train120_combined, X_val120_combined, y_train120, y_val120)

lstm_butter120_extra, _ = train_model(metadata120_orig, butter_train120, 
                                lstm_butter120, fit_butter120_params)

Epoch 1/100
1211/1211 [==============================] - 13s 11ms/step - loss: 0.9438 - precision_1: 0.5527 - recall_1: 0.9806 - val_loss: 1.0895 - val_precision_1: 0.4456 - val_recall_1: 0.9615
Epoch 2/100
1211/1211 [==============================] - 13s 11ms/step - loss: 0.9167 - precision_1: 0.5598 - recall_1: 0.9813 - val_loss: 1.0836 - val_precision_1: 0.4455 - val_recall_1: 0.9548
Epoch 3/100
1211/1211 [==============================] - 13s 11ms/step - loss: 0.9090 - precision_1: 0.5632 - recall_1: 0.9795 - val_loss: 1.0648 - val_precision_1: 0.4438 - val_recall_1: 0.9508
Epoch 4/100
1211/1211 [==============================] - 13s 11ms/step - loss: 0.9006 - precision_1: 0.5668 - recall_1: 0.9760 - val_loss: 1.0826 - val_precision_1: 0.4449 - val_recall_1: 0.9526
Epoch 5/100
1211/1211 [==============================] - 13s 11ms/step - loss: 0.8967 - precision_1: 0.5689 - recall_1: 0.9755 - val_loss: 0.9781 - val_precision_1: 0.4344 - val_recall_1: 0.8920
Epoch 6/100
1211/1211 [==

In [34]:
fit_butter120_params = (400, 128, 300, class_weight)

metadata120_combined = (X_train120_combined, X_val120_combined, y_train120, y_val120)

lstm_butter120_extra, _ = train_model(metadata120_orig, butter_train120, 
                                lstm_butter120, fit_butter120_params)

Epoch 201/300
1211/1211 [==============================] - 13s 11ms/step - loss: 0.6693 - precision_1: 0.6773 - recall_1: 0.9435 - val_loss: 1.3815 - val_precision_1: 0.4571 - val_recall_1: 0.7464
Epoch 202/300
1211/1211 [==============================] - 13s 11ms/step - loss: 0.6716 - precision_1: 0.6767 - recall_1: 0.9424 - val_loss: 1.3232 - val_precision_1: 0.4540 - val_recall_1: 0.7671
Epoch 203/300
1211/1211 [==============================] - 13s 11ms/step - loss: 0.6725 - precision_1: 0.6767 - recall_1: 0.9422 - val_loss: 1.4478 - val_precision_1: 0.4492 - val_recall_1: 0.7653
Epoch 204/300
1211/1211 [==============================] - 13s 11ms/step - loss: 0.6722 - precision_1: 0.6771 - recall_1: 0.9426 - val_loss: 1.4083 - val_precision_1: 0.4510 - val_recall_1: 0.7562
Epoch 205/300
1211/1211 [==============================] - 13s 11ms/step - loss: 0.6685 - precision_1: 0.6780 - recall_1: 0.9422 - val_loss: 1.3655 - val_precision_1: 0.4546 - val_recall_1: 0.7724
Epoch 206/300
1

In [48]:
lstmc120_combined = create_lstm((120, 7))
class_weight = {0: 1, 1: len(y_train120)/sum(y_train120)}
fit_butter120_params = (100, 128, 0, class_weight)

metadata120_combined = (X_train120_combined, X_val120_combined, y_train120, y_val120)

lstmc120_combined, _ = train_model(metadata120_orig, butter_train120, 
                                lstmc120_combined, fit_butter120_params)

Epoch 1/100
 481/1211 [==========>...................] - ETA: 8s - loss: 1.4333 - precision_15: 0.5467 - recall_15: 0.9984 - auc: 0.5221

KeyboardInterrupt: 

### Classification of sequences of length 240

In [16]:
raw_train240, data_index240 = prepare_dynamic_dataset(split_data, 240)

butter_train240, _ = prepare_dynamic_dataset(butter_data, 240)

X_index240 = pd.DataFrame(data_index240, columns=['fileindex']
                                   ).reset_index()

X_train240 = X_train_orig.merge(X_index240, how='inner', on='fileindex')
y_train240 = X_train240.DYS.astype(int)

X_val240 = X_val_orig.merge(X_index240, how='inner', on='fileindex')
y_val240 = X_val240.DYS.astype(int)

X_train240_extra = X_train_extra.merge(X_index240, how='inner', on='fileindex')
y_train240_extra = X_train240_extra.DYS.astype(int)

X_val240_extra = X_val_extra.merge(X_index240, how='inner', on='fileindex')
y_val240_extra = X_val240_extra.DYS.astype(int)

In [20]:
lstm_butter240 = create_simple_lstm((240, 7))
class_weight = {0: 1, 1: len(y_train240)/sum(y_train240)}
fit_butter240_params = (100, 256, 0, class_weight)

metadata240 = (X_train240, X_val240, y_train240, y_val240)

lstm_butter240, _ = train_model(metadata240, butter_train240, 
                                lstm_butter240, fit_butter240_params)

Epoch 1/100
584/584 [==============================] - 18s 27ms/step - loss: 1.2558 - precision_4: 0.1660 - recall_4: 0.8369 - val_loss: 0.6810 - val_precision_4: 0.3096 - val_recall_4: 0.9426
Epoch 2/100
584/584 [==============================] - 15s 26ms/step - loss: 1.2423 - precision_4: 0.1700 - recall_4: 0.8672 - val_loss: 0.6735 - val_precision_4: 0.3360 - val_recall_4: 0.9178
Epoch 3/100
584/584 [==============================] - 15s 26ms/step - loss: 1.2337 - precision_4: 0.1760 - recall_4: 0.8366 - val_loss: 0.6703 - val_precision_4: 0.3118 - val_recall_4: 0.8473
Epoch 4/100
584/584 [==============================] - 15s 26ms/step - loss: 1.2266 - precision_4: 0.1796 - recall_4: 0.8268 - val_loss: 0.6589 - val_precision_4: 0.2884 - val_recall_4: 0.6822
Epoch 5/100
584/584 [==============================] - 15s 26ms/step - loss: 1.2260 - precision_4: 0.1815 - recall_4: 0.8084 - val_loss: 0.6694 - val_precision_4: 0.2725 - val_recall_4: 0.6268
Epoch 6/100
584/584 [==============

In [21]:
lstm_butter240_extra = create_simple_lstm((240, 7))
class_weight = {0: 1, 1: len(y_train240_extra)/sum(y_train240_extra)}
fit_butter240_params = (100, 256, 0, class_weight)

metadata240_extra = (X_train240_extra, X_val240_extra, y_train240_extra, y_val240_extra)

lstm_butter240_extra, _ = train_model(metadata240_extra, butter_train240, 
                                lstm_butter240_extra, fit_butter240_params)

Epoch 1/100
527/527 [==============================] - 16s 26ms/step - loss: 0.8903 - precision_5: 0.5542 - recall_5: 0.9774 - val_loss: 0.8272 - val_precision_5: 0.4295 - val_recall_5: 0.9022
Epoch 2/100
527/527 [==============================] - 13s 25ms/step - loss: 0.8819 - precision_5: 0.5587 - recall_5: 0.9680 - val_loss: 0.8752 - val_precision_5: 0.4291 - val_recall_5: 0.9057
Epoch 3/100
527/527 [==============================] - 13s 25ms/step - loss: 0.8773 - precision_5: 0.5586 - recall_5: 0.9706 - val_loss: 0.8286 - val_precision_5: 0.4361 - val_recall_5: 0.9187
Epoch 4/100
527/527 [==============================] - 13s 25ms/step - loss: 0.8759 - precision_5: 0.5593 - recall_5: 0.9700 - val_loss: 0.8350 - val_precision_5: 0.4259 - val_recall_5: 0.8630
Epoch 5/100
527/527 [==============================] - 13s 25ms/step - loss: 0.8745 - precision_5: 0.5629 - recall_5: 0.9640 - val_loss: 0.8083 - val_precision_5: 0.4229 - val_recall_5: 0.8585
Epoch 6/100
527/527 [==============

### Classification of sequences of length 480

In [22]:
raw_train480, data_index480 = prepare_dynamic_dataset(split_data, 480)

butter_train480, _ = prepare_dynamic_dataset(butter_data, 480)

X_index480 = pd.DataFrame(data_index480, columns=['fileindex']
                                   ).reset_index()

X_train480 = X_train_orig.merge(X_index480, how='inner', on='fileindex')
y_train480 = X_train480.DYS.astype(int)

X_val480 = X_val_orig.merge(X_index480, how='inner', on='fileindex')
y_val480 = X_val480.DYS.astype(int)

X_train480_extra = X_train_extra.merge(X_index480, how='inner', on='fileindex')
y_train480_extra = X_train480_extra.DYS.astype(int)

X_val480_extra = X_val_extra.merge(X_index480, how='inner', on='fileindex')
y_val480_extra = X_val480_extra.DYS.astype(int)

In [25]:
lstm_butter480_extra = create_simple_lstm((480, 7))

class_weight = {0: 1, 1: len(y_train480_extra)/sum(y_train480_extra)}
fit_butter480_params = (300, 128, 0, class_weight)

metadata480_extra = (X_train480_extra, X_val480_extra, y_train480_extra, y_val480_extra)

lstm_butter480_extra, _ = train_model(metadata480_extra, butter_train480, 
                                lstm_butter480_extra, fit_butter480_params)

Epoch 101/200
766/766 [==============================] - 31s 38ms/step - loss: 0.9997 - precision_7: 0.5589 - recall_7: 0.9930 - val_loss: 0.8799 - val_precision_7: 0.4229 - val_recall_7: 0.8688
Epoch 102/200
766/766 [==============================] - 29s 37ms/step - loss: 0.9864 - precision_7: 0.5649 - recall_7: 0.9906 - val_loss: 0.8951 - val_precision_7: 0.4281 - val_recall_7: 0.8527
Epoch 103/200
766/766 [==============================] - 29s 37ms/step - loss: 0.9795 - precision_7: 0.5676 - recall_7: 0.9903 - val_loss: 0.9179 - val_precision_7: 0.4344 - val_recall_7: 0.8733
Epoch 104/200
766/766 [==============================] - 29s 37ms/step - loss: 0.9760 - precision_7: 0.5672 - recall_7: 0.9918 - val_loss: 0.8825 - val_precision_7: 0.4268 - val_recall_7: 0.7867
Epoch 105/200
766/766 [==============================] - 29s 37ms/step - loss: 0.9801 - precision_7: 0.5654 - recall_7: 0.9921 - val_loss: 0.8867 - val_precision_7: 0.4370 - val_recall_7: 0.8688
Epoch 106/200
766/766 [==

I don't think there is enough data to support larger sequence length, already were padding the shorter sequences in the original dataset by a considerable amount.

#### QD adopted architecture

In [35]:
from keras.models import Sequential
from keras.layers import LSTM, Dense, Conv1D, MaxPool1D


def create_three_block(input_shape):
    optimizer = tf.keras.optimizers.Adamax(learning_rate=0.002)
    metrics = [tf.keras.metrics.Precision(),
           tf.keras.metrics.Recall()]
    
    lstm = Sequential([
            LSTM(128, input_shape=input_shape,
                                 return_sequences=True, dropout=0.1),
            Conv1D(kernel_size=5, filters=32, input_shape=input_shape), 
            MaxPool1D(5),
            LSTM(64, input_shape=input_shape,
                                 return_sequences=True, dropout=0.1),
            Conv1D(kernel_size=5, filters=32, input_shape=input_shape), 
            MaxPool1D(2),
            LSTM(32, dropout=0.1),
            Dense(16, activation='relu'),
            Dense(1, activation='sigmoid')])

    lstm.compile(optimizer=optimizer,
              loss=tf.losses.BinaryCrossentropy(),
              metrics=metrics)
    return lstm

In [36]:
three_block_lstm = create_three_block((480, 7))

class_weight = {0: 1, 1: len(y_train480_extra)/sum(y_train480_extra)}
fit_butter480_params = (300, 128, 200, class_weight)

metadata480_extra = (X_train480_extra, X_val480_extra, y_train480_extra, y_val480_extra)

lstm_butter480_extra, _ = train_model(metadata480_extra, butter_train480, 
                                three_block_lstm, fit_butter480_params)

Epoch 201/300


2023-08-31 20:47:26.253117: I tensorflow/tsl/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory


766/766 [==============================] - 30s 34ms/step - loss: 0.8693 - precision_11: 0.5672 - recall_11: 0.9813 - val_loss: 0.9099 - val_precision_11: 0.4302 - val_recall_11: 0.9405
Epoch 202/300
766/766 [==============================] - 25s 33ms/step - loss: 0.8524 - precision_11: 0.5728 - recall_11: 0.9810 - val_loss: 0.9604 - val_precision_11: 0.4186 - val_recall_11: 0.8599
Epoch 203/300
766/766 [==============================] - 25s 33ms/step - loss: 0.8396 - precision_11: 0.5780 - recall_11: 0.9763 - val_loss: 1.0366 - val_precision_11: 0.4200 - val_recall_11: 0.8479
Epoch 204/300
766/766 [==============================] - 25s 33ms/step - loss: 0.8287 - precision_11: 0.5833 - recall_11: 0.9704 - val_loss: 0.9890 - val_precision_11: 0.4335 - val_recall_11: 0.9393
Epoch 205/300
766/766 [==============================] - 25s 33ms/step - loss: 0.8179 - precision_11: 0.5907 - recall_11: 0.9640 - val_loss: 1.0109 - val_precision_11: 0.4254 - val_recall_11: 0.8791
Epoch 206/300
766/7